In [1]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
!pip install --upgrade huggingface_hub
!pip install diffusers
!pip install transformers
!pip install accelerate 
!pip install scipy 
!pip install safetensors 
!pip install xformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 15.8 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 934.9/934.9 kB 51.2 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.0/7.0 MB 94.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 121.5 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 215.3/215.3 kB 15.4 MB/s eta 0:00:00
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
    

In [3]:
import torch
from PIL import Image
from io import BytesIO
from os import makedirs, listdir

from diffusers import StableDiffusionImg2ImgPipeline

from os.path import exists, join

In [4]:
if exists("/content/drive/MyDrive/ORT/Tésis Máster/Codes/datasets/generated_datasets/pneumoconiosis/diffusion/StableDiffusionV2"):
  WORK_DIR = "/content/drive/MyDrive/ORT/Tésis Máster/Codes/datasets/generated_datasets/pneumoconiosis/diffusion/StableDiffusionV2"
  DATA_DIR = '/content/drive/MyDrive/ORT/Tésis Máster/Codes/datasets/transformed_datasets/pneumoconiosis/pneumoconiosis_resized/train/1'
else:
  WORK_DIR = "/content/drive/MyDrive/ORT/Tesis/Codes/datasets/generated_datasets/pneumoconiosis/diffusion/StableDiffusionV2"
  DATA_DIR = '/content/drive/MyDrive/ORT/Tesis/Codes/datasets/transformed_datasets/pneumoconiosis/pneumoconiosis_resized/train/1'

print(WORK_DIR)
print(DATA_DIR)

/content/drive/MyDrive/ORT/Tésis Máster/Codes/datasets/generated_datasets/pneumoconiosis/diffusion/StableDiffusionV2
/content/drive/MyDrive/ORT/Tésis Máster/Codes/datasets/transformed_datasets/pneumoconiosis/pneumoconiosis_resized/train/1


In [5]:
DEVICE = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
DEVICE

device(type='cuda')

In [6]:
model_id_or_path = "stabilityai/stable-diffusion-2-1"
pipe = StableDiffusionImg2ImgPipeline.from_pretrained(model_id_or_path, safety_checker=None, torch_dtype=torch.float16)
pipe = pipe.to(DEVICE)

Fetching 13 files:   0%|          | 0/13 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/transformers/models/clip/feature_extraction_clip.py:28: FutureWarning: The class CLIPFeatureExtractor is deprecated and will be removed in version 5 of Transformers. Please use CLIPImageProcessor instead.
  warnings.warn(


In [7]:
# Check type of GPU and VRAM available.
!nvidia-smi --query-gpu=name,memory.total,memory.free --format=csv,noheader

Tesla T4, 15360 MiB, 11652 MiB


In [14]:
# 50 only seems to work only for small noises and 0.8 (default noise) it's too much
noises_added = [0.05, 0.10, 0.15, 0.2]
inferences_steps = [24, 50]

In [ ]:
g_cuda = torch.Generator(device=DEVICE)
g_cuda.manual_seed(1337)

In [15]:
for na in noises_added:
    print(f">> {na}")
    for infs in inferences_steps:
        if (na == 0.05 and infs == 50) or (infs != 50):
            print(f">>>> {infs}")
            noise_str = f'noise_{na}_{infs}'
            if not exists(join(WORK_DIR, noise_str)):
                makedirs(join(WORK_DIR, noise_str))
            for image in listdir(DATA_DIR):
                init_image = Image.open(join(DATA_DIR,image)).convert("RGB")
                prompt = "a chest-xray image"
                images = pipe(prompt=prompt, image=init_image, strength=na, guidance_scale=7.5, num_inference_steps=infs, generator=g_cuda).images
                images[0].convert('L').save(join(WORK_DIR, noise_str, f'noise_{na}_{infs}_{image}'))

>> 0.05
>>>> 24


  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

...

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]

  0%|          | 0/4 [00:00<?, ?it/s]